### Importazioni

In [5]:
from dotenv import dotenv_values
import json
import requests

## Estraggo le coordinate dai POI

In [96]:
# Apro il file e leggo il contenuto
with open('DICTIONARYTOTALE.txt', 'r') as file:
    contenuto = file.read()

In [97]:
# Decodifico il contenuto JSON in un dizionario Python
dizionario = json.loads(contenuto)

# Lista per le coordinate
coordinate = []

# Estraggo le longitudini e latitudini e le aggiungo alla lista coordinate
for elemento in dizionario.values():
    latitudine = elemento.get('lat')
    longitudine = elemento.get('lon')
    if latitudine is not None and longitudine is not None:
        coordinate.append((latitudine, longitudine))

# Stampo la lista delle coordinate
print(coordinate)

[(42.68827, 12.549764), (42.683333, 12.55), (42.690376, 12.54649), (42.691138, 12.54658), (42.69067, 12.546327), (42.70388888888889, 12.574444444444444), (42.698055555555555, 12.531388888888888), (42.673620035730664, 12.5873151), (42.673169, 12.603323), (42.656894, 12.536004), (42.7100669, 12.4951428), (42.70867, 12.48504), (42.664167, 12.508611), (42.71342, 12.50648), (42.711472, 12.611841), (42.708, 12.621), (42.65, 12.55), (42.64827, 12.637932), (42.73033, 12.58681), (42.7847, 12.0356), (42.786111, 12.037778), (42.772684, 12.039017), (42.771667, 12.018611), (42.804302, 12.071065), (42.75527777777778, 12.001666666666667), (42.80222222222222, 11.983888888888888), (42.833333, 12.066667), (42.835532, 12.065821), (42.816667, 11.966667), (42.755278, 11.945833), (42.7919, 11.9175), (42.7805, 11.9067), (42.587742, 12.295626), (42.583333, 12.3), (42.591907, 12.25983), (42.574862, 12.32824), (42.616667, 12.3), (42.566667, 12.333333), (42.62388, 12.29671), (42.621667, 12.254444), (42.546496, 1

In [98]:
print(str(len(coordinate)) + " POI")

3141 POI


In [99]:
poche_coordinate = coordinate[300:400]

print(poche_coordinate)

[(42.8577, 12.36638), (42.864011, 12.454119), (42.92333333333333, 12.464166666666666), (42.86483055555556, 12.473430555555556), (43.094735, 12.318536), (43.104167, 12.313889), (43.09475, 12.3315), (43.113153, 12.343253), (43.083749, 12.343877), (43.103056, 12.350278), (43.085259, 12.346622), (43.105, 12.3515), (43.0732, 12.3332), (43.102428, 12.355897), (43.110322, 12.259767), (43.128238, 12.287518), (43.129027, 12.287718), (43.133333, 12.283333), (43.13333333333333, 12.283333333333333), (43.13333333333333, 12.283333333333333), (43.13333333333333, 12.283333333333333), (43.07059, 12.23871), (43.360409, 12.712378), (43.349421, 12.72444), (43.3683, 12.7457), (43.3683, 12.7457), (43.37169, 12.748431), (43.331111, 12.742222), (43.399444, 12.751389), (43.37712, 12.78352), (43.4, 12.66), (43.403889, 12.666111), (43.4112, 12.659), (42.982174, 12.42015), (42.9824, 12.4197), (42.983333, 12.416667), (42.982824, 12.429597), (42.96436, 12.40257), (42.98839, 12.38819), (42.96477, 12.44562), (43.0100

In [100]:
print(len(poche_coordinate))

100


## Recupero la chiave API

In [6]:
dotenv = dotenv_values()
api_key = dotenv.get("API_KEY");

print(api_key)

8A20587981B148ADBBF3BED91ACFC937


## Estraggo i POI presenti su TripAdvisor

In [80]:
# Creo un insieme per memorizzare gli ID già presenti nel file
id_presenti = set()

# Controllo se il file esiste
import os
# Se il file esiste, leggo il contenuto attuale del file e memorizzo gli ID
if os.path.exists('poi.txt'):
    with open('poi.txt', 'r') as file:
        for line in file:
            # Divido la riga usando ': ' come separatore solo alla prima occorrenza
            id, resto = line.strip().split(': ', 1)
            # Divido il resto della riga usando ', ' come separatore per ottenere il nome del POI
            nome = resto.split(', ')[0]
            id_presenti.add(id)
   
            

# Creo la lista vuota di POI da salvare
poi = []

# Mi salvo nella lista l'id e il nome del POI solo se l'id non è già presente
for coordinate in poche_coordinate:
    url = "https://api.content.tripadvisor.com/api/v1/location/nearby_search?latLong=" + str(coordinate[0]) + "%2C" + str(coordinate[1]) + "&key=" + api_key + "&category=attractions&language=it"
    headers = {"accept": "application/json"}
    response = requests.get(url, headers=headers)
   
    POI = response.json()

    # Estraggo l'id e il nome di ciascun POI e li aggiungo alla lista di POI se l'id non è già presente
    for elemento in POI['data']:
        nome = elemento.get('name')
        id = elemento.get('location_id')
        citta = elemento.get('address_obj')
        if nome is not None and id is not None and id not in id_presenti:
            poi.append((id, nome, citta))
            # Aggiungo l'id all'insieme degli ID presenti
            id_presenti.add(id)

# Apro il file in modalità scrittura in modalità append
with open('poi.txt', 'a', encoding='utf-8') as file:
    # Itero sulla lista di POI e scrivo ciascun POI nel file solo se l'id non è già presente
    for id, nome, citta in poi:
        file.write(f"{id}: {nome}, {citta}\n")

print(poi)
    

[('19094673', 'Chiesa di San Sabino', {'street1': 'Via Roma 6', 'street2': '', 'city': 'Fratta Todina', 'state': 'Provincia di Perugia', 'country': 'Italia', 'postalcode': '06054', 'address_string': 'Via Roma 6, 06054 Fratta Todina Italia'}), ('21235121', 'Masseria Felicia', {'street1': 'Sp 104 - Loc San Terenzano', 'street2': 'Frazione Carano', 'city': 'Sessa Aurunca', 'state': 'Provincia di Caserta', 'country': 'Italia', 'postalcode': '', 'address_string': 'Sp 104 - Loc San Terenzano Frazione Carano, Sessa Aurunca Italia'}), ('17608585', 'Chiesa della Madonna delle Grazie', {'street1': 'Via Montegrappa', 'street2': 'San Terenziano', 'city': 'Gualdo Cattaneo', 'state': 'Provincia di Perugia', 'country': 'Italia', 'postalcode': '06035', 'address_string': 'Via Montegrappa San Terenziano, 06035, Gualdo Cattaneo Italia'}), ('5930936', 'bar dello sport', {'street1': 'via roma 88', 'street2': '', 'city': 'San Terenziano', 'state': 'Provincia di Perugia', 'country': 'Italia', 'postalcode': '

In [104]:
print(len(poi))

205


In [1]:
# Inizializzo un dizionario vuoto per memorizzare gli ID e i nomi dei POI
poi_dict = {}

# Leggo il contenuto del file riga per riga
with open('poi.txt', 'r', encoding='latin-1') as file:
    for line in file:
        # Divido la riga usando ': ' come separatore solo alla prima occorrenza
        id, resto = line.strip().split(': ', 1)
        # Divido il resto della riga usando ', ' come separatore per ottenere il nome del POI
        nome = resto.split(', ')[0]
        # Aggiungo l'id e il nome al dizionario
        poi_dict[id] = nome

# Ora poi_dict conterrà gli ID come chiavi e i nomi dei POI come valori
print(poi_dict)


{'8666261': 'Palazzo Cesi', '13436625': 'Chiesa di Santa Cecilia', '21223808': 'Lago Di Arezzo', '19071050': 'Frantoio Oleario Palmadori Massimo', '2016179': 'Carsulae - Parco Archeologico', '19487544': 'Chiesa San Bernardino', '19485030': 'Chiesa di Santï¿½Apollinare', '21389509': 'Chiesa San Faustino', '17785314': "Pieve di Sant'Antonio Abate", '17780645': "Chiesa di Sant'Antonio Abate", '17781582': "Chiesa Di Sant'antonio Abate", '617225': "Velia's Cooking Style", '11851556': 'Bottega del Castello della Sale', '10384019': 'Cirulli - Aziende Agricole', '12673247': 'Castello di Madonna Antonia', '17780814': 'chiesa della S.S. Annunziata', '27514189': 'Parrucchiera Giulia', '13436641': 'Museo dei Cicli Geologici', '13436639': 'Chiesa di San Michele Arcangelo', '13436560': "Chiesa della Madonna dell'Acqua", '4828006': 'Borgo Antico Bar', '10727071': 'Chiesa Santa Maria Assunta', '26437754': 'Shiatsuqi di Natascia Minciarelli', '26628676': 'Le Fontane - Lavatoio pubblico', '17780615': 'A

In [2]:
len(poi_dict)

712

In [3]:
for elemento in poi_dict:
    print(elemento)

8666261
13436625
21223808
19071050
2016179
19487544
19485030
21389509
17785314
17780645
17781582
617225
11851556
10384019
12673247
17780814
27514189
13436641
13436639
13436560
4828006
10727071
26437754
26628676
17780615
23603031
26454141
23498616
17785149
23527414
17784926
8442796
6362879
3316846
10751519
6873086
13506803
23736060
5988820
13908621
8818259
15234702
19486021
19485904
21129953
15234713
7927400
19635998
12827750
5937150
13908574
26858943
26848269
10717566
23590891
24077147
21129964
19485106
15582334
15582326
12941174
15582304
12941300
20943988
4178733
15582352
9974289
14902761
10536774
15582310
17567725
10125575
21330794
21341165
23082361
21341156
23082363
15582323
21341167
21341166
4103928
20947702
10120122
7117226
1583158
23919722
21272422
23066524
23430908
21330795
21329540
4131906
23410936
19485109
15843151
10821335
6878472
12819225
10820447
10820435
10820353
19940269
19344024
10342709
23682565
25336273
24033005
3400132
1392223
20724089
20724098
11502819
13436659
66091

In [88]:
len(poi_dict)

712

### Salvo i POI in un dizionario JSON

In [108]:
# salvo il dizionario in un file json
dizionario_json = "poi.json"

# Salvataggio del dizionario nel file JSON
with open(dizionario_json, "w") as file:
    json.dump(poi_dict, file)

In [9]:
poi_dict[506:]

TypeError: unhashable type: 'slice'

## Recupero le recensioni relative ai POI estratti

In [13]:
items_list = list(poi_dict.items())
print(items_list)

for elemento in items_list[506:]:
    print(elemento[0])


[('8666261', 'Palazzo Cesi'), ('13436625', 'Chiesa di Santa Cecilia'), ('21223808', 'Lago Di Arezzo'), ('19071050', 'Frantoio Oleario Palmadori Massimo'), ('2016179', 'Carsulae - Parco Archeologico'), ('19487544', 'Chiesa San Bernardino'), ('19485030', 'Chiesa di Santï¿½Apollinare'), ('21389509', 'Chiesa San Faustino'), ('17785314', "Pieve di Sant'Antonio Abate"), ('17780645', "Chiesa di Sant'Antonio Abate"), ('17781582', "Chiesa Di Sant'antonio Abate"), ('617225', "Velia's Cooking Style"), ('11851556', 'Bottega del Castello della Sale'), ('10384019', 'Cirulli - Aziende Agricole'), ('12673247', 'Castello di Madonna Antonia'), ('17780814', 'chiesa della S.S. Annunziata'), ('27514189', 'Parrucchiera Giulia'), ('13436641', 'Museo dei Cicli Geologici'), ('13436639', 'Chiesa di San Michele Arcangelo'), ('13436560', "Chiesa della Madonna dell'Acqua"), ('4828006', 'Borgo Antico Bar'), ('10727071', 'Chiesa Santa Maria Assunta'), ('26437754', 'Shiatsuqi di Natascia Minciarelli'), ('26628676', '

In [14]:
# Dizionario per memorizzare le recensioni per ogni location
recensioni_per_location = {}

items_list = list(poi_dict.items())
# Itero sui POI e recupera le recensioni
for elemento in items_list[505:]:
    url = "https://api.content.tripadvisor.com/api/v1/location/" + elemento[0] + "/reviews?key=" + api_key + "&language=it"
    headers = {"accept": "application/json"}
    response = requests.get(url, headers=headers)
    REC = response.json()

    # Estraggo le recensioni di ciascun POI e le aggiungo al dizionario
    for elemento in REC['data']:
        id_rec = elemento.get('id')
        id_loc = elemento.get('location_id')
        rating = elemento.get('rating')
        recensione = elemento.get('text')

        # Se la location_id non è già presente nel dizionario, l'aggiungo come chiave con una lista vuota come valore
        if id_loc not in recensioni_per_location:
            recensioni_per_location[id_loc] = {}

        # Aggiungo la recensione al dizionario nidificato utilizzando l'id della recensione come chiave
        recensioni_per_location[id_loc][id_rec] = {'rating': rating, 'recensione': recensione}

# Scrivo il dizionario di recensioni su un file JSON
with open('recensioni_per_location.json', 'w') as file:
    json.dump(recensioni_per_location, file)

In [15]:
REC

{'data': [{'id': 735268158,
   'lang': 'it',
   'location_id': 6154915,
   'published_date': '2019-12-29T05:24:10Z',
   'rating': 5,
   'helpful_votes': 0,
   'rating_image_url': 'https://www.tripadvisor.com/img/cdsi/img2/ratings/traveler/s5.0-66827-5.svg',
   'url': 'https://www.tripadvisor.it/ShowUserReviews-g2634111-d6154915-r735268158-Reviews-Nikka_Figo-Sant_Eraclio_Foligno_Province_of_Perugia_Umbria.html?m=66827#review735268158',
   'text': 'Sempre una garanzia. Magliette ottime e servizi clienti sempre impeccabile. Grazie davvero e alla prossima maglietta.',
   'title': 'Magliette di ottima qualità',
   'trip_type': 'Per affari',
   'travel_date': '2019-12-31',
   'user': {'username': 'Culture730175',
    'user_location': {'id': 'null'},
    'avatar': {'thumbnail': 'https://media-cdn.tripadvisor.com/media/photo-t/1a/f6/e2/a7/default-avatar-2020-44.jpg',
     'small': 'https://media-cdn.tripadvisor.com/media/photo-l/1a/f6/e2/a7/default-avatar-2020-44.jpg',
     'medium': 'https://

In [16]:
len(recensioni_per_location)

155

In [17]:
# Apro il file in modalità lettura
with open('recensioni_per_location.json', 'r') as file:
    recensioni = file.read();
    # Decodifico il contenuto JSON in un dizionario Python

print(recensioni)
print(len(recensioni))
dizionario_recensioni = json.loads(recensioni)

{"7051888": {"773938056": {"rating": 5, "recensione": "Abitando a pochi chilometri, ho scoperto questa attrazione grazie proprio a Tripadvisor. Purtroppo non c\u2019\u00e8 la bench\u00e9 minima indicazione, una recensione lo spiega ma Tripadvisor la traduce male. Provo a descriverla meglio: uscendo dalla superstrada (uscita Ripabianca), proseguire verso Collepepe; arrivati alla rotatoria prendere l\u2019uscita verso la localit\u00e0 \u201ccarceri\u201d (prima uscita); proseguire e, appena passato il sottopassaggio, girare a sinistra su una strada bianca in salita. A quel punto proseguire fino a raggiungere l\u2019ultima casa sulla sinistra, a destra c\u2019\u00e8 una strada che si insinua all\u2019interno di un boschetto. Ebbene, sulla destra si trover\u00e0 la prima cisterna (si vede una recinzione, basta fare il giro l\u2019ingresso si trova dietro), la seconda si trova sulla sinistra sotto una tettoia. Purtroppo la prima \u00e8 chiusa ma si intravede qualcosa, mentre la seconda \u00

In [18]:
dizionario_recensioni

{'7051888': {'773938056': {'rating': 5,
   'recensione': 'Abitando a pochi chilometri, ho scoperto questa attrazione grazie proprio a Tripadvisor. Purtroppo non c’è la benché minima indicazione, una recensione lo spiega ma Tripadvisor la traduce male. Provo a descriverla meglio: uscendo dalla superstrada (uscita Ripabianca), proseguire verso Collepepe; arrivati alla rotatoria prendere l’uscita verso la località “carceri” (prima uscita); proseguire e, appena passato il sottopassaggio, girare a sinistra su una strada bianca in salita. A quel punto proseguire fino a raggiungere l’ultima casa sulla sinistra, a destra c’è una strada che si insinua all’interno di un boschetto. Ebbene, sulla destra si troverà la prima cisterna (si vede una recinzione, basta fare il giro l’ingresso si trova dietro), la seconda si trova sulla sinistra sotto una tettoia. Purtroppo la prima è chiusa ma si intravede qualcosa, mentre la seconda è libera. \nDa queste cisterne (facenti parte di una villa romana ormai

In [59]:
type(dizionario_recensioni)

dict

In [19]:
# recupero anche il dizionario con solo chiave univoca della location e il nome
with open('poi.json', 'r') as file:
    poi_json = file.read()
    dizionario_poi = json.loads(poi_json)

In [20]:
type(dizionario_poi)

dict

In [21]:
dizionario_poi.items()

dict_items([('8666261', 'Palazzo Cesi'), ('13436625', 'Chiesa di Santa Cecilia'), ('21223808', 'Lago Di Arezzo'), ('19071050', 'Frantoio Oleario Palmadori Massimo'), ('2016179', 'Carsulae - Parco Archeologico'), ('19487544', 'Chiesa San Bernardino'), ('19485030', 'Chiesa di Sant\x92Apollinare'), ('21389509', 'Chiesa San Faustino'), ('17785314', "Pieve di Sant'Antonio Abate"), ('17780645', "Chiesa di Sant'Antonio Abate"), ('17781582', "Chiesa Di Sant'antonio Abate"), ('617225', "Velia's Cooking Style"), ('11851556', 'Bottega del Castello della Sale'), ('10384019', 'Cirulli - Aziende Agricole'), ('12673247', 'Castello di Madonna Antonia'), ('17780814', 'chiesa della S.S. Annunziata'), ('27514189', 'Parrucchiera Giulia'), ('13436641', 'Museo dei Cicli Geologici'), ('13436639', 'Chiesa di San Michele Arcangelo'), ('13436560', "Chiesa della Madonna dell'Acqua"), ('4828006', 'Borgo Antico Bar'), ('10727071', 'Chiesa Santa Maria Assunta'), ('26437754', 'Shiatsuqi di Natascia Minciarelli'), ('

In [22]:
dizionario_recensioni

{'7051888': {'773938056': {'rating': 5,
   'recensione': 'Abitando a pochi chilometri, ho scoperto questa attrazione grazie proprio a Tripadvisor. Purtroppo non c’è la benché minima indicazione, una recensione lo spiega ma Tripadvisor la traduce male. Provo a descriverla meglio: uscendo dalla superstrada (uscita Ripabianca), proseguire verso Collepepe; arrivati alla rotatoria prendere l’uscita verso la località “carceri” (prima uscita); proseguire e, appena passato il sottopassaggio, girare a sinistra su una strada bianca in salita. A quel punto proseguire fino a raggiungere l’ultima casa sulla sinistra, a destra c’è una strada che si insinua all’interno di un boschetto. Ebbene, sulla destra si troverà la prima cisterna (si vede una recinzione, basta fare il giro l’ingresso si trova dietro), la seconda si trova sulla sinistra sotto una tettoia. Purtroppo la prima è chiusa ma si intravede qualcosa, mentre la seconda è libera. \nDa queste cisterne (facenti parte di una villa romana ormai

In [23]:
for items in dizionario_poi.items():
    for idloc, recensione_info in dizionario_recensioni.items():
        recensione_info = {'POI': "nome_poi", **recensione_info}

In [24]:
for items in dizionario_poi.items():
    for recensione in dizionario_recensioni.items():
        print(items[1])

Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi
Palazzo Cesi

In [25]:
for id_rec, recensione_info in dizionario_recensioni.items():
    # Controllo se l'id della recensione corrisponde a un id del POI
    if id_rec in dizionario_poi:
        # Ottengo il nome del POI associato all'id del POI
        nome_poi = dizionario_poi[id_rec]
        # Aggiungo il nome del POI all'inizio della recensione
        recensione_info = {'POI': nome_poi, **recensione_info}
        # Aggiorno il dizionario delle recensioni con la recensione aggiornata
        dizionario_recensioni[id_rec] = recensione_info

# Ora dizionario_recensioni contiene il campo 'POI' aggiunto all'inizio di ciascuna recensione



In [49]:
dizionario_recensioni


{'8666261': {'POI': 'Palazzo Cesi',
  '917883573': {'rating': 4,
   'recensione': 'Palazzo Cesi di Acquasparta é il principale monumento del borgo.\nVisitabile con un esiguo biglietto di 6 euro, venne fondato dal Duca Federico Cesi nel Seicento, e nelle sue sale venne ospitato Galileo Galilei.\nIl prospetto esterno, che dà sulla piazza principale, si presenta, nell’ordine inferiore, con uno splendido portale rinascimentale a tutto sesto, ornato da una cornice in conci bugnati.\nL’interno é impreziosito da un susseguirsi di sale che presentano splendide volte affrescate, in eccellente stato di conservazione, mentre altre sono ornate da elaborati soffitti lignei. Gli affreschi presenti, narrano vicende legate alla mitologia.\nLa struttura del palazzo é edificata su due piani, piano terra e primo piano, entrambi visitabili. Splendido é anche il loggiato del primo piano, ove si affacciano le stanze. Le varie sale che si susseguono nel percorso di visita sono  consequenziali tra loro, sia a

In [26]:
# Scrivo il dizionario di recensioni su un file JSON
with open('recensioni_complete.json', 'w') as file:
    json.dump(dizionario_recensioni, file)

In [27]:
data.items()

NameError: name 'data' is not defined

In [28]:
# Conto le recensioni estratte per ora

with open('recensioni_complete.json', 'r', encoding='utf-8') as file:
    data = json.load(file)

# Inizializzo il contatore delle recensioni
numero_recensioni = 0

# Itero attraverso i dati ed estraggo le recensioni
for poi_id, poi_data in data.items():
    for recensione_id, recensione_info in poi_data.items():
        if isinstance(recensione_info, dict) and 'recensione' in recensione_info:
            recensione = recensione_info['recensione']
            print(recensione)  # Stampo la recensione 
            numero_recensioni += 1

# Stampa il numero totale di recensioni
print("Numero totale di recensioni:", numero_recensioni)


Abitando a pochi chilometri, ho scoperto questa attrazione grazie proprio a Tripadvisor. Purtroppo non c’è la benché minima indicazione, una recensione lo spiega ma Tripadvisor la traduce male. Provo a descriverla meglio: uscendo dalla superstrada (uscita Ripabianca), proseguire verso Collepepe; arrivati alla rotatoria prendere l’uscita verso la località “carceri” (prima uscita); proseguire e, appena passato il sottopassaggio, girare a sinistra su una strada bianca in salita. A quel punto proseguire fino a raggiungere l’ultima casa sulla sinistra, a destra c’è una strada che si insinua all’interno di un boschetto. Ebbene, sulla destra si troverà la prima cisterna (si vede una recinzione, basta fare il giro l’ingresso si trova dietro), la seconda si trova sulla sinistra sotto una tettoia. Purtroppo la prima è chiusa ma si intravede qualcosa, mentre la seconda è libera. 
Da queste cisterne (facenti parte di una villa romana ormai inesistente) si capisce quanta storia nascosta vi sia in I